In [20]:
import pandas as pd
import numpy as np
import os
from projdirs import datadir, optdir

DATA = pd.read_csv(datadir + r'TEST DATA\SAM_60min\086282TMY_60min_SAM.csv',skiprows=2)
solar = DATA['global horizontal irradiance'].copy().tolist()
wind = DATA['wind speed'].copy().tolist()


from PACKAGE.optimisation import make_dzn_file, optimise

simparams = dict(DT = 3600,#s
                 ETA_EL = 0.80,
                 BAT_ETA_in = 0.95,
                 BAT_ETA_out = 0.95,
                 C_PV = 0.6,#$/W
                 C_W = 1.6, #$/W
                 C_EL = 0.5, #$/W
                 C_HS = 16, #$/kgH
                 C_BAT = 50/1000/3600, #($/W.s)
                 CF = 0.99,
                 S = solar,
                 W = wind,
                 L = [0.1 for i in range(len(solar))])#kgH/s


results = optimise(simparams)

print ('CAPEX = %0.2f [M$]' %(float(results['CAPEX'][0])/1e6))
print ('pv_max = %0.2f [MW]' %(float(results['pv_max'][0]/1e6)))
print ('w_max = %0.2f [MW]' %(float(results['w_max'][0]/1e6)))
print ('el_max = %0.4f [MW]' %(float(results['el_max'][0]/1e6)))
print ('hs_max = %0.2f [T of H2]' %(float(results['hs_max'][0]/1e3)))
print ('bat_capa = %0.2f [MWh]' %(float(results['bat_capa'][0]/(1e6*3600))))
print ('bat_pmax = %0.2f [MW]' %(float(results['bat_pmax'][0])/1e6))


data_plot = pd.DataFrame(dict(t= np.arange(0,len(simparams['S'])),
                              solar=simparams['S'], wind=simparams['W'],
                              pv_out=results['pv_out'],
                              w_out=results['w_out'],
                              pc=results['pc'],
                              he_out = results['he_out'],
                              hr_out = results['hr_out'],
                              sh = results['sh'][0:-1],
                              R = results['r'][0:-1],
                              L = results['L'],
                              hs_out = results['L']-results['hr_out'],
                              bat_e_stored = results['bat_e_stored'][0:-1],
                              bat_pin = results['bat_pin'],
                              bat_pout = results['bat_pout']
                             ))

data_plot['time'] =pd.to_datetime('2022-01-01') + pd.to_timedelta(data_plot.t, 'h')
data_plot.drop('t',axis=1,inplace=True)


# data_plot

CAPEX = 107.32 [M$]
pv_max = 61.84 [MW]
w_max = 26.73 [MW]
el_max = 37.4577 [MW]
hs_max = 152.07 [T of H2]
bat_capa = 124.58 [MWh]
bat_pmax = 64.93 [MW]


In [ ]:
C_BAT = 50 [$/kWh]
CAPEX = 107.32 [M$]
pv_max = 61.84 [MW]
w_max = 26.73 [MW]
el_max = 37.4577 [MW]
hs_max = 152.07 [T of H2]
bat_capa = 124.58 [MWh]
bat_pmax = 64.93 [MW]

In [ ]:
C_BAT = 75 [$/kWh]
CAPEX = 108.95 [M$]
pv_max = 55.17 [MW]
w_max = 30.36 [MW]
el_max = 47.1539 [MW]
hs_max = 130.77 [T of H2]
bat_capa = 21.34 [MWh]
bat_pmax = 22.46 [MW]

In [ ]:
C_BAT = 100 [$/kWh]
CAPEX = 109.21 [M$]
pv_max = 55.32 [MW]
w_max = 30.46 [MW]
el_max = 49.8802 [MW]
hs_max = 130.43 [t of H2]
bat_capa = 2.60 [MWh]

In [ ]:
C_BAT = 150 [$/kWh]
CAPEX = 109.24 [M$]
pv_max = 56.06 [MW]
w_max = 30.14 [MW]
el_max = 50.5084 [MW]
hs_max = 132.21 [T of H2]
bat_capa = 0.00 [MWh]
bat_pmax = 0.00 [MW]

In [ ]:
C_BAT = 200 [$/kWh]
CAPEX = 109.24 [M$]
pv_max = 56.06 [MW]
w_max = 30.14 [MW]
el_max = 50.5084 [MW]
hs_max = 132.21 [t of H2]
bat_capa = 0.00 [MWh]

In [16]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
#               line_shape='hv', name='Solar Irrad.'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.sh),
              name='Stored H',yaxis="y1"),
                )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.R),
              name='R',yaxis="y1")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.he_out),
              line_shape='hv',name='he_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hs_out),
              line_shape='hv',name='hs_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hr_out),
              line_shape='hv',name='hr_out',yaxis="y2")
                )



fig.update_layout(
    yaxis1=dict(
        range=[0, max(data_plot.sh)]
    ),
    yaxis2=dict(
        range=[0, 0.4]
    )
    
)
    

fig.show()

In [112]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
              line_shape='hv', name='Solar Irrad.', yaxis="y2"),
                )

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pv_out),
              line_shape='hv', name='pv_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.w_out),
              line_shape='hv', name='w_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pc),
              line_shape='hv', name='pc'),
                )




# fig.update_layout(
#     yaxis1=dict(
#         range=[0, 15000]
#     ),
#     yaxis2=dict(
#         range=[0, 0.4]
#     )
    
# )
    

fig.show()


In [32]:
results.keys()

dict_keys(['CAPEX', 'pv_max', 'w_max', 'el_max', 'hs_max', 'pv_out', 'w_out', 'pc', 'he_out', 'hr_out', 'sh', 'r', 'L'])